In [2]:
import pandas as pd
import numpy as np
import os
import sumolib
import copy
from tqdm import tqdm
from datetime import datetime

In [27]:
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
fmins = range(midnight, next_day, 300)
m = 105 # m ranges from 26 to 287
# sigtable 시작시각  : 현재시각 - 1200 = 08:25
# 시뮬레이션 시작시각 : 현재시각 - 900 = 08:30
# 시뮬레이션 종료시각 : 현재시각 - 600 = 08:35
# 현재시각           : 08:45
present_time = fmins[m]
sigtable_start = fmins[m] - 1200
sim_start = fmins[m] - 900
sim_end = fmins[m] - 600
print(datetime.fromtimestamp(sigtable_start))
print(datetime.fromtimestamp(sim_start))
print(datetime.fromtimestamp(sim_end))
print(datetime.fromtimestamp(present_time))
net = sumolib.net.readNet('../../Data/networks/sn.net.xml')
inter_node = pd.read_csv('../../data/tables/inter_node.csv', index_col=0)
match6 = pd.read_csv('../../Data/tables/matching/match6.csv', index_col=0)
match6 = match6[['node_id', 'phase_no', 'ring_type', 'inc_edge', 'out_edge']].reset_index(drop=True)
histid = pd.read_csv(f'../../Data/tables/histids/histids_{present_time}.csv', index_col=0)
histid = histid.reset_index(drop=True).drop(columns=['inter_no'])
histid

2024-01-05 08:25:00
2024-01-05 08:30:00
2024-01-05 08:35:00
2024-01-05 08:45:00


In [ ]:
plan = pd.read_csv('../../Data/tables/plan.csv', index_col=0)
node2mincycle = {}
inter2mincycle = {}
for inter_no in sorted(plan.inter_no.unique()):
    inter2mincycle[inter_no] = plan[plan.inter_no==inter_no].cycle.min()
    print(inter_no, inter2mincycle[inter_no])
display(plan)

In [4]:
inter2node = dict(zip(inter_node['inter_no'], inter_node['node_id']))
node2inter = dict(zip(inter_node['node_id'], inter_node['inter_no']))
pa2ch = {'i0':['u00'], 'i1':[], 'i2':['u20'], 'i3':['c30', 'u30', 'u31', 'u32'], 'i6':['u60'], 'i7':[], 'i8':[], 'i9':[]}
node_ids = sorted(inter_node.node_id.unique())
parent_ids = sorted(inter_node[inter_node.inter_type=='parent'].node_id.unique())
nodes = [net.getNode(node_id) for node_id in node_ids]

print(inter2node)
print(node2inter)
print(pa2ch)
print(node_ids)
print(parent_ids)

{175: 'u00', 176: 'i1', 177: 'u20', 178: 'c30', 210: 'u60', 206: 'i7', 201: 'i8', 202: 'i9'}
{'i0': 175, 'u00': 175, 'i1': 176, 'i2': 177, 'u20': 177, 'i3': 178, 'u30': 178, 'u31': 178, 'u32': 178, 'c30': 178, 'i6': 210, 'u60': 210, 'i7': 206, 'i8': 201, 'i9': 202}
{'i0': ['u00'], 'i1': [], 'i2': ['u20'], 'i3': ['c30', 'u30', 'u31', 'u32'], 'i6': ['u60'], 'i7': [], 'i8': [], 'i9': []}
['c30', 'i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9', 'u00', 'u20', 'u30', 'u31', 'u32', 'u60']
['i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9']


In [5]:
def make_histids(histid, match6, parent_ids, pa2ch):
    new_histids = []
    for parent_id in parent_ids:
        for child_id in pa2ch[parent_id]:
            new_histid = histid.copy()[histid.node_id==parent_id]
            new_histid[['inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']] = np.nan
            for i, row in new_histid.iterrows():
                phas_A = row.phas_A
                phas_B = row.phas_B
                new_match = match6[match6.node_id==child_id]
                Arow = new_match[(new_match.phase_no==phas_A) & (new_match.ring_type=='A')]
                if ~ Arow[['inc_edge', 'out_edge']].isna().all().all():
                    inc_edge = Arow.iloc[0].inc_edge
                    out_edge = Arow.iloc[0].out_edge
                    new_histid.loc[i, ['inc_edge_A', 'out_edge_A']] = [inc_edge, out_edge]
                Brow = new_match[(new_match.phase_no==phas_B) & (new_match.ring_type=='B')]
                if ~ Brow[['inc_edge', 'out_edge']].isna().all().all():
                    inc_edge = Brow.iloc[0].inc_edge
                    out_edge = Brow.iloc[0].out_edge
                    new_histid.loc[i, ['inc_edge_B', 'out_edge_B']] = [inc_edge, out_edge]
                new_histid.loc[i, 'node_id'] = child_id
            new_histids.append(new_histid)
    new_histids = pd.concat(new_histids)
    histids = pd.concat([histid.copy(), new_histids])
    histids = histids.sort_values(by=['start_unix', 'node_id', 'phas_A', 'phas_B']).reset_index(drop=True)
    return histids
histids = make_histids(histid, match6, parent_ids, pa2ch)

In [6]:
def initialize_states():
    node2init = {}
    for node in nodes:
        node_id = node.getID()
        conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
        conns = [c for c in conns if c[0] >= 0]
        conns = sorted(conns, key=lambda x: x[0])
        state = []
        for i, ci in conns:
            if ci.getTLLinkIndex() < 0:
                continue
            are_foes = False
            for j, cj in conns:
                if ci.getTo() == cj.getTo():
                    continue
                if node.areFoes(i, j):
                    are_foes = True
                    break
            state.append('r' if are_foes else 'g')
        node2init[node_id] = state

    # 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
    for _, row in histids.iterrows():
        node_id = row['node_id']
        inc_edge_A = row.inc_edge_A
        inc_edge_B = row.inc_edge_B
        out_edge_A = row.out_edge_A
        out_edge_B = row.out_edge_B

        if pd.isna(inc_edge_A) or pd.isna(out_edge_A):
            pass
        else:
            inc_edge_A = net.getEdge(inc_edge_A)
            out_edge_A = net.getEdge(out_edge_A)
            for conn in inc_edge_A.getConnections(out_edge_A):
                index = conn.getTLLinkIndex()
                if index >= 0:
                    node2init[node_id][index] = 'r'

        if pd.isna(inc_edge_B) or pd.isna(out_edge_B):
            pass
        else:
            inc_edge_B = net.getEdge(inc_edge_B)
            out_edge_B = net.getEdge(out_edge_B)
            for conn in inc_edge_B.getConnections(out_edge_B):
                index = conn.getTLLinkIndex()
                if index >= 0:
                    node2init[node_id][index] = 'r'
    return node2init
node2init = initialize_states()

In [7]:
histids[histids.node_id=='u30']

node_id  start_unix  phas_A  phas_B  duration    inc_edge_A    out_edge_A  \
36      u30  1704410790       1       1        38           NaN           NaN   
37      u30  1704410790       2       2        39           NaN           NaN   
38      u30  1704410790       3       3        42           NaN           NaN   
39      u30  1704410790       4       4        21  571556452_01  571556452_02   
94      u30  1704410950       1       1        38           NaN           NaN   
95      u30  1704410950       2       2        39           NaN           NaN   
96      u30  1704410950       3       3        42           NaN           NaN   
97      u30  1704410950       4       4        21  571556452_01  571556452_02   
142     u30  1704411110       1       1        38           NaN           NaN   
143     u30  1704411110       2       2        39           NaN           NaN   
144     u30  1704411110       3       3        42           NaN           NaN   
145     u30  1704411110       4       4        21  571556452_01  571556452_02   
195     u30  1704411270       1       1        38           NaN           NaN   
196     u30  1704411270       2       2        39           NaN           NaN   
197     u30  1704411270       3       3        42           NaN           NaN   
198     u30  1704411270       4       4        21  571556452_01  571556452_02   
248     u30  1704411430       1       1        38           NaN           NaN   
249     u30  1704411430       2       2        39           NaN           NaN   
250     u30  1704411430       3       3        42           NaN           NaN   
251     u30  1704411430       4       4        21  571556452_01  571556452_02   
306     u30  1704411590       1       1        38           NaN           NaN   
307     u30  1704411590       2       2        39           NaN           NaN   
308     u30  1704411590       3       3        42           NaN           NaN   
309     u30  1704411590       4       4        21  571556452_01  571556452_02   

    inc_edge_B out_edge_B  
36         NaN        NaN  
37         NaN        NaN  
38         NaN        NaN  
39         NaN        NaN  
94         NaN        NaN  
95         NaN        NaN  
96         NaN        NaN  
97         NaN        NaN  
142        NaN        NaN  
143        NaN        NaN  
144        NaN        NaN  
145        NaN        NaN  
195        NaN        NaN  
196        NaN        NaN  
197        NaN        NaN  
198        NaN        NaN  
248        NaN        NaN  
249        NaN        NaN  
250        NaN        NaN  
251        NaN        NaN  
306        NaN        NaN  
307        NaN        NaN  
308        NaN        NaN  
309        NaN        NaN

In [8]:
def make_sigtable(histids, node2init, net):
    sigtable = histids.copy()
    sigtable['init_state'] = sigtable['node_id'].map(node2init)
    sigtable['state'] = sigtable['init_state'].map(lambda x:''.join(x))
    for i, row in sigtable.iterrows():
        node_id = row.node_id
        inc_edge_A = row.inc_edge_A
        inc_edge_B = row.inc_edge_B
        out_edge_A = row.out_edge_A
        out_edge_B = row.out_edge_B
        state = copy.deepcopy(node2init)[node_id]
        if pd.isna(inc_edge_A) or pd.isna(out_edge_A):
            pass
        else:
            inc_edge_A = net.getEdge(inc_edge_A)
            out_edge_A = net.getEdge(out_edge_A)
            for conn in inc_edge_A.getConnections(out_edge_A):
                index = conn.getTLLinkIndex()
                if index >= 0:
                    state[index] = 'G'
            sigtable.at[i, 'state'] = ''.join(state)

        if pd.isna(inc_edge_B) or pd.isna(out_edge_B):
            pass
        else:
            inc_edge_B = net.getEdge(inc_edge_B)
            out_edge_B = net.getEdge(out_edge_B)
            for conn in inc_edge_B.getConnections(out_edge_B):
                index = conn.getTLLinkIndex()
                if index >= 0:
                    state[index] = 'G'
            sigtable.at[i, 'state'] = ''.join(state)
    sigtable = sigtable.dropna(subset='state')
    sigtable = sigtable.reset_index(drop=True)
    sigtable['phase_sumo'] = sigtable.groupby(['node_id', 'start_unix']).cumcount()
    sigtable = sigtable[sigtable.start_unix >= sigtable_start]
    sigtable = sigtable[['node_id', 'start_unix', 'phase_sumo', 'duration', 'state']]
    sigtable = sigtable.sort_values(by=['start_unix', 'node_id'])
    sigtable['start_dt'] = sigtable['start_unix'].apply(lambda x:datetime.fromtimestamp(x))
    return sigtable
sigtable = make_sigtable(histids, node2init, net)
display(sigtable)

node_id  start_unix  phase_sumo  duration       state            start_dt
0        i2  1704410739           0        40     GGggGGG 2024-01-05 08:25:39
1        i2  1704410739           1        25     rrggrrr 2024-01-05 08:25:39
2        i2  1704410739           2        71     rrggrrr 2024-01-05 08:25:39
3        i2  1704410739           3        34     rrggGGG 2024-01-05 08:25:39
4       u20  1704410739           0        40      ggrggg 2024-01-05 08:25:39
..      ...         ...         ...       ...         ...                 ...
343     u00  1704411630           3        26   ggggrgggg 2024-01-05 08:40:30
344     u00  1704411630           4        33   ggggrgggg 2024-01-05 08:40:30
345      i1  1704411670           0        37  gGGGGGrgrr 2024-01-05 08:41:10
346      i1  1704411670           1        93  grrGGGGgrr 2024-01-05 08:41:10
347      i1  1704411670           2        40  grrrrrrgGG 2024-01-05 08:41:10

[348 rows x 6 columns]

In [9]:
sigtable = make_sigtable(histids, node2init, net)
display(sigtable[sigtable.node_id=='u32'])

node_id  start_unix  phase_sumo  duration     state            start_dt
44      u32  1704410790           0        38  gggggggG 2024-01-05 08:26:30
45      u32  1704410790           1        39  gggggggr 2024-01-05 08:26:30
46      u32  1704410790           2        42  gggggggr 2024-01-05 08:26:30
47      u32  1704410790           3        21  gggggggr 2024-01-05 08:26:30
102     u32  1704410950           0        38  gggggggG 2024-01-05 08:29:10
103     u32  1704410950           1        39  gggggggr 2024-01-05 08:29:10
104     u32  1704410950           2        42  gggggggr 2024-01-05 08:29:10
105     u32  1704410950           3        21  gggggggr 2024-01-05 08:29:10
150     u32  1704411110           0        38  gggggggG 2024-01-05 08:31:50
151     u32  1704411110           1        39  gggggggr 2024-01-05 08:31:50
152     u32  1704411110           2        42  gggggggr 2024-01-05 08:31:50
153     u32  1704411110           3        21  gggggggr 2024-01-05 08:31:50
203     u32  1704411270           0        38  gggggggG 2024-01-05 08:34:30
204     u32  1704411270           1        39  gggggggr 2024-01-05 08:34:30
205     u32  1704411270           2        42  gggggggr 2024-01-05 08:34:30
206     u32  1704411270           3        21  gggggggr 2024-01-05 08:34:30
256     u32  1704411430           0        38  gggggggG 2024-01-05 08:37:10
257     u32  1704411430           1        39  gggggggr 2024-01-05 08:37:10
258     u32  1704411430           2        42  gggggggr 2024-01-05 08:37:10
259     u32  1704411430           3        21  gggggggr 2024-01-05 08:37:10
314     u32  1704411590           0        38  gggggggG 2024-01-05 08:39:50
315     u32  1704411590           1        39  gggggggr 2024-01-05 08:39:50
316     u32  1704411590           2        42  gggggggr 2024-01-05 08:39:50
317     u32  1704411590           3        21  gggggggr 2024-01-05 08:39:50

In [10]:
def make_Sigtable(sigtable):
    Sigtable = []
    for node_id, group in sigtable.groupby('node_id'):
        new_rows_list = []
        for i in range(1, len(group)):
            prev_row = group.iloc[i-1:i].copy()
            next_row = group.iloc[i:i+1].copy()
            new_rows = pd.concat([prev_row, prev_row, next_row]).reset_index(drop=True)
            new_rows.loc[0, 'phase_sumo'] = str(prev_row.phase_sumo.iloc[0]) + '_g'
            new_rows.loc[0, 'duration'] = new_rows.loc[0, 'duration'] - 5
            new_rows.loc[1, 'phase_sumo'] = str(prev_row.phase_sumo.iloc[0]) + '_y'
            new_rows.loc[1, 'duration'] = 4
            yellow_state = ''
            red_state = ''
            for a, b in zip(prev_row.state.iloc[0], next_row.state.iloc[0]):
                if a == 'G' and b == 'r':
                    yellow_state += 'y'
                    red_state += 'r'
                else:
                    yellow_state += a
                    red_state += a
            new_rows.loc[2, 'phase_sumo'] = str(next_row.phase_sumo.iloc[0]) + '__r'
            new_rows.loc[2, 'duration'] = 1
            new_rows.loc[1, 'state'] = yellow_state
            new_rows.loc[2, 'state'] = red_state
            new_rows_list.append(new_rows)
        next_row['phase_sumo'] = str(next_row.phase_sumo.iloc[0]) + '_g'
        next_row['duration'] -= 5
        # next_row.loc['duration'] -= 5
        new_rows_list.append(next_row)
        new_rows = pd.concat(new_rows_list)
        Sigtable.append(new_rows)
    Sigtable = pd.concat(Sigtable).sort_values(by=['node_id', 'start_unix', 'phase_sumo']).reset_index(drop=True)
    return Sigtable
Sigtable = make_Sigtable(sigtable)
Sigtable

node_id  start_unix phase_sumo  duration      state            start_dt
0        c30  1704410790        0_g        33     rrrrrr 2024-01-05 08:26:30
1        c30  1704410790        0_y         4     rrrrrr 2024-01-05 08:26:30
2        c30  1704410790       1__r         1     rrrrrr 2024-01-05 08:26:30
3        c30  1704410790        1_g        34     GGGGGG 2024-01-05 08:26:30
4        c30  1704410790        1_y         4     GGGGGG 2024-01-05 08:26:30
...      ...         ...        ...       ...        ...                 ...
1011     u60  1704411609       3__r         1  ggggggggr 2024-01-05 08:40:09
1012     u60  1704411609        3_g        60  ggggggggr 2024-01-05 08:40:09
1013     u60  1704411609        3_y         4  ggggggggr 2024-01-05 08:40:09
1014     u60  1704411609       4__r         1  ggggggggr 2024-01-05 08:40:09
1015     u60  1704411609        4_g        18  ggggggggr 2024-01-05 08:40:09

[1016 rows x 6 columns]

In [16]:
inter_node

inter_no node_id inter_type
0        175      i0     parent
1        175     u00      child
2        176      i1     parent
3        177      i2     parent
4        177     u20      child
5        178      i3     parent
6        178     u30      child
7        178     u31      child
8        178     u32      child
9        178     c30      child
10       210      i6     parent
11       210     u60      child
12       206      i7     parent
13       201      i8     parent
14       202      i9     parent

In [10]:
# sigtable 시작시각  : 현재시각 - 1200 = 08:25
# 시뮬레이션 시작시각 : 현재시각 - 900 = 08:30
# 시뮬레이션 종료시각 : 현재시각 - 600 = 08:35
# 현재시각           : 08:45
print(datetime.fromtimestamp(sigtable_start))
print(datetime.fromtimestamp(sim_start))
print(datetime.fromtimestamp(sim_end))
print(datetime.fromtimestamp(present_time))

2024-01-05 08:25:00
2024-01-05 08:30:00
2024-01-05 08:35:00
2024-01-05 08:45:00


In [11]:
def make_SIGTABLE(Sigtable):
    offsets = {}
    SIGTABLE = []
    for node_id, group in Sigtable.groupby('node_id'):
        lsbs = group[group['start_unix'] < sim_start]['start_unix'].max() # the last start_unix before sim_start
        offsets[node_id] = lsbs - sim_start
        group = group[(group['start_unix'] < sim_end) & (group['start_unix'] >= lsbs)]
        SIGTABLE.append(group)
    SIGTABLE = pd.concat(SIGTABLE)

    strings = ['<additional>\n']
    for node_id, group in SIGTABLE.groupby('node_id'):
        strings.append(f'    <tlLogic id="{node_id}" type="static" programID="{node_id}_prog" offset="{offsets[node_id]}">\n')
        for i, row in group.iterrows():
            duration = row.duration
            state = row.state
            strings.append(f'      <phase duration="{duration}" state="{state}"/>\n')
        strings.append('    </tlLogic>\n')
    strings.append('</additional>')
    strings = ''.join(strings)
    # 저장
    path_output = '../../Data/networks/sn.add.xml'
    with open(path_output, 'w') as f:
        f.write(strings)
    return SIGTABLE, strings

In [12]:
SIGTABLE, strings = make_SIGTABLE(Sigtable)
display(SIGTABLE[:40])
print(strings)

node_id  start_unix phase_sumo  duration              state  \
11     c30  1704410950       0__r         1             rrrrrr   
12     c30  1704410950        0_g        33             rrrrrr   
13     c30  1704410950        0_y         4             rrrrrr   
14     c30  1704410950       1__r         1             rrrrrr   
15     c30  1704410950        1_g        34             GGGGGG   
16     c30  1704410950        1_y         4             GGGGGG   
17     c30  1704410950       2__r         1             GGGGGG   
18     c30  1704410950        2_g        37             GGGGGG   
19     c30  1704410950        2_y         4             GGGGGG   
20     c30  1704410950       3__r         1             GGGGGG   
21     c30  1704410950        3_g        16             GGGGGG   
22     c30  1704410950        3_y         4             yyyyyy   
23     c30  1704411110       0__r         1             rrrrrr   
24     c30  1704411110        0_g        33             rrrrrr   
25     c30  1704411110        0_y         4             rrrrrr   
26     c30  1704411110       1__r         1             rrrrrr   
27     c30  1704411110        1_g        34             GGGGGG   
28     c30  1704411110        1_y         4             GGGGGG   
29     c30  1704411110       2__r         1             GGGGGG   
30     c30  1704411110        2_g        37             GGGGGG   
31     c30  1704411110        2_y         4             GGGGGG   
32     c30  1704411110       3__r         1             GGGGGG   
33     c30  1704411110        3_g        16             GGGGGG   
34     c30  1704411110        3_y         4             yyyyyy   
35     c30  1704411270       0__r         1             rrrrrr   
36     c30  1704411270        0_g        33             rrrrrr   
37     c30  1704411270        0_y         4             rrrrrr   
38     c30  1704411270       1__r         1             rrrrrr   
39     c30  1704411270        1_g        34             GGGGGG   
40     c30  1704411270        1_y         4             GGGGGG   
41     c30  1704411270       2__r         1             GGGGGG   
42     c30  1704411270        2_g        37             GGGGGG   
43     c30  1704411270        2_y         4             GGGGGG   
44     c30  1704411270       3__r         1             GGGGGG   
45     c30  1704411270        3_g        16             GGGGGG   
46     c30  1704411270        3_y         4             yyyyyy   
84      i0  1704410950       0__r         1  grrrgrrrgrrrrrgrr   
85      i0  1704410950        0_g        35  gGGrgrrrgGGGGrgrr   
86      i0  1704410950        0_y         4  gyyrgrrrgyyyyrgrr   
87      i0  1704410950       1__r         1  grrrgrrrgrrrrrgrr   

              start_dt  
11 2024-01-05 08:29:10  
12 2024-01-05 08:29:10  
13 2024-01-05 08:29:10  
14 2024-01-05 08:29:10  
15 2024-01-05 08:29:10  
16 2024-01-05 08:29:10  
17 2024-01-05 08:29:10  
18 2024-01-05 08:29:10  
19 2024-01-05 08:29:10  
20 2024-01-05 08:29:10  
21 2024-01-05 08:29:10  
22 2024-01-05 08:29:10  
23 2024-01-05 08:31:50  
24 2024-01-05 08:31:50  
25 2024-01-05 08:31:50  
26 2024-01-05 08:31:50  
27 2024-01-05 08:31:50  
28 2024-01-05 08:31:50  
29 2024-01-05 08:31:50  
30 2024-01-05 08:31:50  
31 2024-01-05 08:31:50  
32 2024-01-05 08:31:50  
33 2024-01-05 08:31:50  
34 2024-01-05 08:31:50  
35 2024-01-05 08:34:30  
36 2024-01-05 08:34:30  
37 2024-01-05 08:34:30  
38 2024-01-05 08:34:30  
39 2024-01-05 08:34:30  
40 2024-01-05 08:34:30  
41 2024-01-05 08:34:30  
42 2024-01-05 08:34:30  
43 2024-01-05 08:34:30  
44 2024-01-05 08:34:30  
45 2024-01-05 08:34:30  
46 2024-01-05 08:34:30  
84 2024-01-05 08:29:10  
85 2024-01-05 08:29:10  
86 2024-01-05 08:29:10  
87 2024-01-05 08:29:10

<additional>
    <tlLogic id="c30" type="static" programID="c30_prog" offset="-50">
      <phase duration="1" state="rrrrrr"/>
      <phase duration="33" state="rrrrrr"/>
      <phase duration="4" state="rrrrrr"/>
      <phase duration="1" state="rrrrrr"/>
      <phase duration="34" state="GGGGGG"/>
      <phase duration="4" state="GGGGGG"/>
      <phase duration="1" state="GGGGGG"/>
      <phase duration="37" state="GGGGGG"/>
      <phase duration="4" state="GGGGGG"/>
      <phase duration="1" state="GGGGGG"/>
      <phase duration="16" state="GGGGGG"/>
      <phase duration="4" state="yyyyyy"/>
      <phase duration="1" state="rrrrrr"/>
      <phase duration="33" state="rrrrrr"/>
      <phase duration="4" state="rrrrrr"/>
      <phase duration="1" state="rrrrrr"/>
      <phase duration="34" state="GGGGGG"/>
      <phase duration="4" state="GGGGGG"/>
      <phase duration="1" state="GGGGGG"/>
      <phase duration="37" state="GGGGGG"/>
      <phase duration="4" state="GGGGGG"/>
      

In [ ]:
def generate_signal():
    